In [1]:
import numpy as np
import matplotlib.pyplot as plt
import scipy

from matplotlib import animation, rc
from IPython.display import HTML
rc('animation', html='jshtml')
import seaborn as sns

#Define plotting style:
sns.set() #Set style
sns.set_style('ticks',{'font.family':'serif', 'font.serif':'Times New Roman'})
sns.set_context('paper', font_scale=2.2)

## Problema 1 (Air Hockey)

<font size=3px>Um disco de massa $m = 200$ g está em repouso no centro de uma mesa quadrada de air hockey de lado $l = 2$ m. O disco é atingido por uma raquete na direção de $\theta = 30^{\circ}$ com a horizontal. Se o tempo de contato entre a raquete e o disco é de $\Delta t = 0,1$ s e a força exercida durante o contato foi de 1 N, determine a trajetória do disco:<br>
    a) Durante o contato com a raquete<br>
    b) Após o contato<br>
    c) Em que instante o disco atingirá uma das laterais da mesa?
</font>

In [2]:
t0  = 0.
tC = 0.1
v0x, v0y = 0.,0.
x0,y0 = 1.,1.
a = 1./0.2
theta = 30.*np.pi/180.
l = 2.

ax = a*np.cos(theta)
ay = a*np.sin(theta)
v1x = v0x + ax*tC
v1y = v0y + ay*tC
x1 = x0 + v0x*tC + (ax*tC**2)/2.
y1 = y0 + v0y*tC + (ay*tC**2)/2.
xF = lambda t: x0 + v0x*t + (ax*t**2)/2. if t <= tC else x1 + v1x*(t-tC)
yF = lambda t: y0 + v0y*t + (ay*t**2)/2. if t <= tC else y1 + v1y*(t-tC)

print('ax = %1.2f m/s^2, ay = %1.2f m/s^2, v1x = %1.2f m/s, v1y = %1.2f m/s, x1 = %1.2f m, y1 = %1.2f m' %(ax,ay,v1x,v1y,x1,y1))

tmin, tmax = 0.,3.
dt = 0.05
tpts = np.linspace(tmin,tmax,100)

fig = plt.figure(figsize=(22,7))
ax1 = plt.subplot(131)
ax1.plot([0.,l,l,0.,0.],[0.,0.,l,l,0.],'-')
pt, = ax1.plot([xF(tmin)],[yF(tmin)],'o',markersize=15)
line1, = ax1.plot([xF(tmin)],[yF(tmin)],'--',linewidth=3)
vec = ax1.quiver([xF(tmin)],[yF(tmin)],[np.cos(theta)],[np.sin(theta)],scale=5.5,alpha = 0.2)
xlabel = ax1.set_xlabel('x (m)')
ylabel = ax1.set_ylabel('y (m)')

ax2 = plt.subplot(132)
xLine, = ax2.plot([tmin],[xF(tmin)],linewidth=4,color='r')
xlabel = ax2.set_xlabel('t (s)')
ylabel = ax2.set_ylabel('x (m)')
ax2.set_xlim(tmin,2*tC)
ax2.set_ylim(xF(tmin),xF(2*tC))

ax3 = plt.subplot(133)
yLine, = ax3.plot([tmin],[yF(tmin)],linewidth=4,color='g')
xlabel = ax3.set_xlabel('t (s)')
ylabel = ax3.set_ylabel('y (m)')
ax3.set_xlim(tmin,2*tC)
ax3.set_ylim(yF(tmin),yF(2*tC))

text = plt.text(0.1,0.9*l,r't = %1.2f s' %tmin)
plt.tight_layout(pad=0.4, w_pad=0.5, h_pad=1.0)


def init():
    line1.set_data([xF(tmin)],[yF(tmin)])
    pt.set_data([xF(tmin)],[yF(tmin)])
    vec.set_offsets([xF(tmin),yF(tmin)])
    xLine.set_data([tmin],[xF(tmin)])
    yLine.set_data([tmin],[yF(tmin)])    
    text.set_text(r't = %1.2f s' %tmin)
    return (pt,line1,vec,xLine,yLine,text)
def animate(i):
    tA = tmin+i*dt
    newpts = np.linspace(tmin,tA,100)
    xPts = [xF(t) for t in newpts]
    yPts = [yF(t) for t in newpts]
    xpt,ypt = xF(newpts[-1]),yF(newpts[-1])
    pt.set_data([xpt],[ypt])
    line1.set_data(xPts,yPts)
    vec.set_offsets([xpt,ypt])
    xLine.set_data(newpts,xPts)
    yLine.set_data(newpts,yPts)    
    
    text.set_text(r't = %1.2f s' %tA)    
    if tA > tC:
        vec.set_offsets([2*l,2*l])
        
    return (pt,line1,vec,xLine,yLine,text)


anim = animation.FuncAnimation(fig, animate, init_func=init,
                               frames=int((tmax-tmin)/dt), interval=150, 
                               blit=True)
plt.close()
anim
# plt.show()

ax = 4.33 m/s^2, ay = 2.50 m/s^2, v1x = 0.43 m/s, v1y = 0.25 m/s, x1 = 1.02 m, y1 = 1.01 m


/home/lessa/.local/lib/python3.7/site-packages/matplotlib/tight_layout.py:181: UserWarning: Tight layout not applied. The bottom and top margins cannot be made large enough to accommodate all axes decorations. 
  warnings.warn('Tight layout not applied. '


## Problema 2 (Força de Atrito)

<font size=3px>Dois blocos de massa $M_1$ e $M_2$ estão um sobre o outro e deslizam em um plano inclinado, conforme mostra a figura. O coeficiente de atrito estátio entre o bloco e o plano é $\mu_s = 0,4$ e o coeficiente de atrito cinético é $\mu_k = 0,2$.<br>
(a) Faça um diagrama de forças para cada bloco. <br>
(b) Determine o ângulo máximo para que o sistema esteja em equilíbrio.<br>
(c) Se $\theta = 60^\circ$ e os blocos deslizam juntos (mesma aceleração), determine a aceleração do sistema.<br>
(d) Para a situação do item acima, determine o módulo da força de atrito entre os blocos, se $M_1 = 2$ kg.
</font>
<img src="blocksPlane2.jpg" alt="Drawing" style="width: 300px;"/>

## Problema 3 (Tensão)

<font size=3px>Dado o sistema abaixo, determine:<br>
(a) o diagrama de forças para cada bloco <br>
(b) o valor de $m_B$ (em função de $m_A,\theta_1,\theta_2$) para que o sistema fique em equilíbrio.
</font>
<img src="blocksPlane.jpg" alt="Drawing" style="width: 300px;"/>

## Problema 2 (Movimento Circular)

<font size=3px>Um corpo pequeno de massa m está suspenso por um fio de comprimento $L$.<br>
O corpo gira em um círculo horizontal de raio $r$ com velocidade constante $v$, como mostrado na figura.
Encontrar:<br>
(a) a velocidade do corpo <br>
(b) o período de revolução (1 volta)
</font>
<img src="penduloConico.png" alt="Drawing" style="width: 300px;"/>

### Problema 3 (Movimento Circular)

<font size=3px>Um carro de $1800$ kg passa sobre uma lombada na rua que segue o arco de uma circunferência de raio $20,4$ m como se mostra na figura.<br>
    (a) Qual é a força que a rua exerce sobre o carro quando ele passa pelo ponto mais alto da lombada a
        uma velocidade de $30$ km/h?<br>
    (b) Qual é a máxima velocidade que o carro pode ter passando pelo ponto mais alto da
lombada sem perder contato com a rua?
</font>

### Problema 4 (Movimento Circular e Atrito)

<font size=3px>Uma moeda de massa $3,1$ g fica sobre um pequeno bloco de $20$ g, que por sua vez, descansa sobre um disco giratório. Os coeficientes de atrito entre o bloco e o disco são: $0,75$ (estático) e $0,64$ (cinético). Entre a moeda e o bloco os coeficientes de atrito são: $0,52$ (estático) e $0,45$ (cinético).
Qual seria a máxima taxa de rotação (em revoluções por minuto) que o disco pode ter sem que o bloco ou a moeda escorreguem encima do disco?
</font>
<img src="movimentoCircularAtrito.png" alt="Drawing" style="width: 300px;"/>